In [1]:
from selenium import webdriver
from selenium.webdriver.chrome.options import Options
from bs4 import BeautifulSoup
import json
from tqdm import tqdm

import time
import pandas as pd



In [2]:
BASE_URL = 'https://www.91mobiles.com'
HOME_URL = 'https://www.91mobiles.com/mobile-price-list-in-india'
PROXY = "socks5://127.0.0.1:9150"

#chromium setup for selenium
chrome_options = Options()
chrome_options.add_argument("--headless")
chrome_options.add_argument("--disable-gpu")
chrome_options.add_argument("--proxy-server={}".format(PROXY))
chrome_options.add_argument("--js-flags={}".format("--expose-gc"))
driver = webdriver.Chrome(
    'C:\Dev\Michael\Mobile-Phone-Dataset-GSMArena\chromedriver.exe', options=chrome_options)
driver.set_window_size(1280, 1024)
driver.get(HOME_URL)
driver.implicitly_wait(10)

driver.execute_script('window.scrollTo(0, document.body.scrollHeight)')


In [ ]:
phone_names = []
source = driver.page_source
while True:
    try:
        time.sleep(10)
        pagination = driver.find_element_by_class_name('listing-btns')
        buttons = pagination.find_elements_by_class_name('list-bttnn')

        for button in buttons:
            if button.text == 'Next':
                next_button = button
        results = BeautifulSoup(driver.page_source, 'html.parser')
        finder_results = results.find(
            'div', id='finderResults')
        phones = finder_results.find_all('li')
        for phone in phones:
            phone_names.append(phone.a.get('href'))
        
        
        driver.execute_script(
            'arguments[0].scrollIntoView(true); window.scrollBy(0, -60);', next_button)
        next_button.click()
    except:
        break

        


In [ ]:
phone_names

In [ ]:
hrefs = pd.DataFrame(data=phone_names, columns=['href'])
hrefs.to_csv('hrefs.csv', index=False)

In [3]:
hrefs = pd.read_csv('irisdownhref.csv')


In [4]:
BASE_URL = 'https://www.91mobiles.com'
href_list = hrefs['href'].tolist()

In [5]:
href_list

['/lava-xolo-q900s-price-in-india',
 '/asus-zenfone-4-price-in-india',
 '/htc-desire-616-price-in-india',
 '/karbonn-a91-price-in-india',
 '/philips-w3500-price-in-india',
 '/huawei-honor-3c-price-in-india',
 '/oppo-r1-price-in-india',
 '/lava-xolo-q3000-price-in-india',
 '/datawind-pocketsurfer-3g5-price-in-india',
 '/yxtel-k008-price-in-india',
 '/gionee-elife-e7-price-in-india',
 '/lenovo-vibe-z-price-in-india',
 '/lava-xolo-q2000-price-in-india',
 '/lava-xolo-a500s-ips-price-in-india',
 '/lava-xolo-a600-price-in-india',
 '/intex-cloud-x5-price-in-india',
 '/adcom-thunder-a500-price-in-india',
 '/micromax-bolt-a58-price-in-india',
 '/karbonn-a90-price-in-india',
 '/karbonn-titanium-s6-price-in-india',
 '/samsung-galaxy-golden-price-in-india',
 '/lg-optimus-g2-price-in-india',
 '/micromax-x281-price-in-india',
 '/micromax-a177-canvas-juice-price-in-india',
 '/micromax-canvas-blaze-hd-eg116-price-in-india',
 '/intex-aqua-i15-price-in-india',
 '/micromax-canvas-beat-a114r-price-in-indi

In [6]:
href_list_test = ['/samsung-galaxy-m52-5g-price-in-india']
errors = []
phones_dict_list = []
for i, href in enumerate(tqdm(href_list_test)):
    phone_dict = {}
    driver.execute_script("window.gc()")
    driver.get(BASE_URL + href)
    phone = BeautifulSoup(driver.page_source, 'html.parser')
    name = phone.find('h1','h1_pro_head')
    phone_dict.update({'Name': name.text})
    prices = phone.find('div', class_='det_top_prices')
    store_prc = prices.findAll('span', 'store_prc')
    if store_prc == []:
        try:
            phone = BeautifulSoup(driver.page_source, 'html.parser')
            prices = phone.find('div', class_='spec_rvw_pnl das_bdr')
            store_prc = prices.findAll('span', 'big_prc')
            store_prc = [prc.text.strip() for prc in store_prc]
            store_prc = store_prc[1]
            phone_dict.update({'Price': store_prc})
        except:
            phone_dict.update({'Price': -1})
            pass
    else:
        store_prc = [prc.text.strip().replace('Rs. ', '') for prc in store_prc]
        phone_dict.update({'Price': store_prc})
    tables = phone.findAll('table', class_='spec_table')
    
    for index, table in enumerate(tqdm(tables)):
        trs = table.findAll('tr')
        for tr in trs:
            td = tr.findAll('td')
            try:
                key = td[0].text.strip()
                value = td[1].text.strip()
                phone_dict.update({key : value})
            except:
                errors.append(key)
                pass
    phones_dict_list.append(phone_dict)


100%|██████████| 1/1 [00:08<00:00,  8.89s/it]


In [6]:
errors = []
phones_dict_list = []
for i, href in enumerate(tqdm(href_list)):
    phone_dict = {}
    driver.execute_script("window.gc()")
    driver.get(BASE_URL + href)
    phone = BeautifulSoup(driver.page_source, 'html.parser')
    name = phone.find('h1', 'h1_pro_head')
    phone_dict.update({'Name': name.text})
    prices = phone.find('div', class_='det_top_prices')
    store_prc = prices.findAll('span', 'store_prc')
    if store_prc == []:
        try:
            phone = BeautifulSoup(driver.page_source, 'html.parser')
            prices = phone.find('div', class_='spec_rvw_pnl das_bdr')
            store_prc = prices.findAll('span', 'big_prc')
            store_prc = [prc.text.strip() for prc in store_prc]
            store_prc = store_prc[1]
            phone_dict.update({'Price': store_prc})
        except:
            phone_dict.update({'Price': -1})
            pass
    else:
        store_prc = [prc.text.strip().replace('Rs. ', '') for prc in store_prc]
        phone_dict.update({'Price': store_prc})
    tables = phone.findAll('table', class_='spec_table')

    for index, table in enumerate(tqdm(tables)):
        trs = table.findAll('tr')
        for tr in trs:
            td = tr.findAll('td')
            try:
                key = td[0].text.strip()
                value = td[1].text.strip()
                phone_dict.update({key: value})
            except:
                errors.append(key)
                pass
    phones_dict_list.append(phone_dict)


100%|██████████| 1782/1782 [2:52:34<00:00,  5.81s/it]


In [18]:
phones_dict_list

[{'Name': 'Vivo Y51s',
  'Price': -1,
  'RAM': '6 GB',
  'Processor': 'Samsung Exynos 8 Octa 880',
  'Rear Camera': '48 MP + 2 MP + 2 MP',
  'Front Camera': '8 MP',
  'Battery': '4500 mAh',
  'Display': '6.53 inches',
  'Operating System': 'Android v10 (Q)',
  'Custom UI': 'Funtouch OS',
  'Chipset': 'Samsung Exynos 8 Octa 880',
  'CPU': 'Octa core (2 GHz, Dual core, Cortex A77 + 1.8 GHz, Hexa Core, Cortex A55)',
  'Architecture': '64 bit',
  'Fabrication': '8 nm',
  'Graphics': 'Mali-G76 MP5',
  'RAM Type': 'LPDDR4X',
  'Display Type': 'IPS LCD',
  'Screen Size': '6.53 inches (16.59 cm)',
  'Resolution': '8 MP f/2.0 Primary Camera',
  'Aspect Ratio': '19.5:9',
  'Pixel Density': '395 ppi',
  'Screen to Body Ratio (calculated)': '84.17 %',
  'Bezel-less display': 'Yes with punch-hole display',
  'Touch Screen': 'Yes, Capacitive Touchscreen, Multi-touch',
  'Screen to Body Ratio (claimed by the brand)': '90.7 %',
  'Height': '162 mm\n                                                     

In [7]:
some_df = pd.DataFrame.from_dict(phones_dict_list)


In [8]:
some_df.tail()

Name   Price     RAM     Processor Rear Camera  \
1777   Motorola FlipOut  16,990  512 MB  TI OMAP 3410      3.2 MP   
1778      Micromax X235   3,499     NaN           NaN      0.3 MP   
1779      Micromax X215   2,449     NaN           NaN      0.3 MP   
1780      Micromax X250   3,999     NaN           NaN      0.3 MP   
1781  i-smart i1-Desire   5,999    2 GB           NaN        5 MP   

     Front Camera   Battery      Display        Launch Date  \
1777          NaN  1170 mAh   2.8 inches      June 15, 2010   
1778          NaN  1050 mAh     2 inches     March 21, 2010   
1779          NaN  1800 mAh  1.44 inches  December 29, 2009   
1780          NaN  1300 mAh     2 inches       May 17, 2009   
1781         5 MP  2600 mAh   5.5 inches                NaN   

           Operating System  ... Wi-Fi Calling Waterproof Ruggedness Stylus  \
1777           Android v2.1  ...           NaN        NaN        NaN    NaN   
1778                    NaN  ...           NaN        NaN        NaN    NaN   
1779                    NaN  ...           NaN        NaN        NaN    NaN   
1780                    NaN  ...           NaN        NaN        NaN    NaN   
1781  Android v7.0 (Nougat)  ...           NaN        NaN        NaN    NaN   

     SIM 3 Video Recording Features Wireless Charging Heart Rate Monitor  \
1777   NaN                      NaN               NaN                NaN   
1778   NaN                      NaN               NaN                NaN   
1779   NaN                      NaN               NaN                NaN   
1780   NaN                      NaN               NaN                NaN   
1781   NaN                      NaN               NaN                NaN   

     Software Based Aperture Camera Type  
1777                     NaN         NaN  
1778                     NaN         NaN  
1779                     NaN         NaN  
1780                     NaN         NaN  
1781                     NaN         NaN  

[5 rows x 104 columns]

In [21]:
some_df.to_csv('lava-down.csv')
some_df.to_json('lava-down.json')


In [23]:
driver.quit()